In [1]:
import pandas as pd
import json
import time
from kafka import KafkaProducer
###############preprocessing################
fitdf=pd.read_csv('hourly_fitbit_sema_df_unprocessed.csv')
fitdf = fitdf.dropna(axis=1, thresh=0.5*len(fitdf))
fitdf.head()
unique_id = fitdf['id'].unique()
# print('Number of unique id: ', len(unique_id))
fitdf = fitdf.drop('Unnamed: 0', axis=1)
fitdf.head()

C:\Users\dell\AppData\Local\Temp\ipykernel_4912\125899761.py:6: DtypeWarning: Columns (5,10,19,20) have mixed types. Specify dtype option on import or set low_memory=False.
  fitdf=pd.read_csv('hourly_fitbit_sema_df_unprocessed.csv')


Number of unique id:  71


id        date  hour  calories  distance        bpm  \
0  621e2e8e67b776a24055b564  2021-05-24   0.0     89.04      98.3  66.874763   
1  621e2e8e67b776a24055b564  2021-05-24   1.0     65.62       0.0  58.711364   
2  621e2e8e67b776a24055b564  2021-05-24   2.0     65.40       NaN  55.133495   
3  621e2e8e67b776a24055b564  2021-05-24   3.0     69.01      11.0  60.488613   
4  621e2e8e67b776a24055b564  2021-05-24   4.0     65.73       0.0  59.110638   

  mindfulness_session  steps  age gender  bmi  
0               False  134.0  <30   MALE  <19  
1               False    0.0  <30   MALE  <19  
2               False    NaN  <30   MALE  <19  
3               False   15.0  <30   MALE  <19  
4               False    0.0  <30   MALE  <19

In [2]:
# count nulls
# print('Number of missing values in each column:')
# print(fitdf.isnull().sum())


Number of missing values in each column:
id                         0
date                       0
hour                       0
calories                 460
distance               66375
bpm                    63389
mindfulness_session      396
steps                  66375
age                    13412
gender                  7579
bmi                    13412
dtype: int64


In [ ]:
# get columns date hour and mindfulness_session

In [8]:
# replace the nulls in mindfulness_session with notRecorded
fitdf['mindfulness_session'] = fitdf['mindfulness_session'].fillna('notRecorded')
# display the data types
# print('Data types of the columns:')
# 2021-05-24 the date column is in this format and there is a nother column called hour its float
# with values of 0-23
fitdf['date'] = pd.to_datetime(fitdf['date'])
fitdf['hour'] = fitdf['hour'].astype(int)
# print(fitdf.dtypes)
# fitdf.head()



Data types of the columns:
id                             object
date                   datetime64[ns]
hour                            int32
calories                      float64
distance                      float64
bpm                           float64
mindfulness_session            object
steps                         float64
age                            object
gender                         object
bmi                            object
dtype: object


id       date  hour  calories  distance        bpm  \
0  621e2e8e67b776a24055b564 2021-05-24     0     89.04      98.3  66.874763   
1  621e2e8e67b776a24055b564 2021-05-24     1     65.62       0.0  58.711364   
2  621e2e8e67b776a24055b564 2021-05-24     2     65.40       NaN  55.133495   
3  621e2e8e67b776a24055b564 2021-05-24     3     69.01      11.0  60.488613   
4  621e2e8e67b776a24055b564 2021-05-24     4     65.73       0.0  59.110638   

  mindfulness_session  steps  age gender  bmi  
0               False  134.0  <30   MALE  <19  
1               False    0.0  <30   MALE  <19  
2               False    NaN  <30   MALE  <19  
3               False   15.0  <30   MALE  <19  
4               False    0.0  <30   MALE  <19

In [11]:
# get columns date hour and mindfulness_session
fitdf = fitdf[['date', 'hour', 'mindfulness_session']]
# fitdf.head()
sorted_df = fitdf.sort_values(by=['date', 'hour'])
# sorted_df.head()

date  hour mindfulness_session
159392 2021-04-08    13         notRecorded
159393 2021-04-08    13         notRecorded
159403 2021-04-09    12         notRecorded
159400 2021-04-09    14         notRecorded
159386 2021-04-10    12         notRecorded

In [13]:
# concate date and hour
sorted_df['date_hour'] = sorted_df['date'].astype(str) + ' ' + sorted_df['hour'].astype(str)
sorted_df['date_hour'] = pd.to_datetime(sorted_df['date_hour'])
sorted_df = sorted_df.drop(['date', 'hour'], axis=1)
# sorted_df.head()
sorted_df['mindfulness_session'].value_counts()

KeyError: 'date'

In [16]:
sorted_df=sorted_df.reset_index(drop=True)
# sorted_df.head()

mindfulness_session           date_hour
0         notRecorded 2021-04-08 13:00:00
1         notRecorded 2021-04-08 13:00:00
2         notRecorded 2021-04-09 12:00:00
3         notRecorded 2021-04-09 14:00:00
4         notRecorded 2021-04-10 12:00:00

In [18]:
# for each unique date_hour get subset of the data

BROKER_URL = 'localhost:9092'
TOPIC_NAME = 'mindf'
producer = KafkaProducer(
    bootstrap_servers=BROKER_URL,
    value_serializer=lambda v: json.dumps(v).encode('utf-8')  # Serialize data as JSON
)
uniqueDateHour = sorted_df['date_hour'].unique()
print('Number of unique date_hour: ', len(uniqueDateHour))
for i in range(0, len(uniqueDateHour)):
    # print('Date_hour: ', uniqueDateHour[i])
    subset=sorted_df[sorted_df['date_hour'] == uniqueDateHour[i]]
    subsett=subset.to_dict(orient='records')
    producer.send(TOPIC_NAME, value=subsett)
    time.sleep(10)  # Sleep for 1 second
    print('Sent a subset of data to Kafka')
    

Number of unique date_hour:  5945
Date_hour:  2021-04-08 13:00:00
  mindfulness_session           date_hour
0         notRecorded 2021-04-08 13:00:00
1         notRecorded 2021-04-08 13:00:00
-----------------------------------
Date_hour:  2021-04-09 12:00:00
  mindfulness_session           date_hour
2         notRecorded 2021-04-09 12:00:00
-----------------------------------
Date_hour:  2021-04-09 14:00:00
  mindfulness_session           date_hour
3         notRecorded 2021-04-09 14:00:00
-----------------------------------
Date_hour:  2021-04-10 12:00:00
  mindfulness_session           date_hour
4         notRecorded 2021-04-10 12:00:00
-----------------------------------
Date_hour:  2021-04-10 14:00:00
  mindfulness_session           date_hour
5         notRecorded 2021-04-10 14:00:00
-----------------------------------
Date_hour:  2021-04-12 13:00:00
  mindfulness_session           date_hour
6         notRecorded 2021-04-12 13:00:00
-----------------------------------
Date_hour:  